In [ ]:
#adapting code from https://github.com/hlynurd/lda-for-magic/blob/master/lda-mtg-notebook.ipynb

In [1]:
#importing useful libraries
import pandas as pd
import gensim
import numpy as np
import re
from six import iteritems

In [2]:
#want to look at all 305 cards rather than just the first couple and last couple
pd.set_option('display.max_rows', 500)

In [3]:
#load data
read_df=pd.read_csv("card-win-rates-2020-11-08.csv")

In [4]:
#take only games where neither player mulliganed
clean_games=read_df[read_df['num_mulligans'] + read_df['opp_num_mulligans']==0].reset_index(drop=True)
#separate out wins and losses
wins=clean_games[clean_games['won']==True]
losses=clean_games[clean_games['won']==False]

In [5]:
#look at just deck inclusions
win_deck=wins.iloc[:,623:928]
lose_deck=losses.iloc[:,623:928]
clean_deck=clean_games.iloc[:,623:928]
#use this to iterate through the three different dataframes
dfs=[win_deck,lose_deck,clean_deck]

In [6]:
#cleaning up the column names
new_col_names=[]
for name in win_deck.columns:
    new_col_names.append(name[5:])
for df in dfs:
    df.columns=new_col_names


In [7]:
# #seeing what happens if I drop basic lands
# for df in dfs:
#     df.drop(columns=['Swamp','Island','Mountain','Forest','Plains'],inplace=True)

In [8]:
#creating a dictionary of cards in the set
dictionary = gensim.corpora.Dictionary([win_deck.columns])

In [9]:
#checking dictionary
for i in dictionary:
    print(dictionary[i])

Acquisitions Expert
Adventure Awaits
Agadeem's Awakening
Agadeem, the Undercrypt
Akiri, Fearless Voyager
Akoum Hellhound
Akoum Teeth
Akoum Warrior
Allied Assault
Ancient Greenwarden
Angel of Destiny
Angelheart Protector
Anticognition
Archon of Emeria
Archpriest of Iona
Ardent Electromancer
Ashaya, Soul of the Wild
Attended Healer
Bala Ged Recovery
Bala Ged Sanctuary
Base Camp
Beyeen Coast
Beyeen Veil
Blackbloom Bog
Blackbloom Rogue
Blood Beckoning
Blood Price
Bloodchief's Thirst
Boulderloft Pathway
Branchloft Pathway
Brightclimb Pathway
Broken Wings
Brushfire Elemental
Bubble Snare
Canopy Baloth
Canyon Jerboa
Cascade Seer
Charix, the Raging Isle
Chilling Trap
Cinderclasm
Cleansing Wildfire
Clearwater Pathway
Cleric of Chill Depths
Cleric of Life's Bond
Cliffhaven Kitesail
Cliffhaven Sell-Sword
Concerted Defense
Confounding Conundrum
Coralhelm Chronicler
Coveted Prize
Cragcrown Pathway
Cragplate Baloth
Crawling Barrens
Cunning Geysermage
Dauntless Survivor
Dauntless Unity
Deadly Allianc

In [10]:
#making column names into the index, need to do this to make a corpus
new_cols_as_index=[*range(win_deck.shape[1])]
for df in dfs:
    df.columns=new_cols_as_index



In [11]:
#class that creates the corpus object
class MyCorpus(object):
    #pass the dataframe you want to use
    def __init__(self,_dframe):
        self.clean_deck=_dframe
    #append non-zero values as (index of card,# of card) tuples
    def __iter__(self):
        for index,line in self.clean_deck.iterrows():
            my_line=[]
            for i,val in zip(range(self.clean_deck.shape[1]),line):
                if val > 0:
                    my_line.append((i,val))
            yield my_line

In [12]:
#create corpuses for wins, losses, and all decks
win_corpus=MyCorpus(win_deck)
lose_corpus=MyCorpus(lose_deck)
all_corpus=MyCorpus(clean_deck)
#checking to see if it's in the right format
for i in lose_corpus:
    print(i)

[(25, 1), (27, 1), (56, 1), (69, 1), (72, 1), (75, 1), (76, 1), (84, 1), (87, 3), (139, 1), (142, 2), (152, 1), (154, 8), (189, 1), (222, 1), (242, 2), (258, 8), (260, 1), (275, 1), (276, 1), (288, 1), (291, 1)]
[(25, 1), (27, 1), (56, 1), (69, 1), (72, 1), (75, 1), (76, 1), (84, 1), (87, 3), (139, 1), (142, 2), (152, 1), (154, 8), (189, 1), (222, 1), (242, 2), (258, 8), (260, 1), (275, 1), (276, 1), (288, 1), (291, 1)]
[(25, 1), (27, 1), (56, 1), (69, 1), (72, 1), (75, 1), (76, 1), (84, 1), (87, 3), (139, 1), (142, 2), (152, 1), (154, 8), (189, 1), (222, 1), (242, 2), (258, 8), (260, 1), (275, 1), (276, 1), (288, 1), (291, 1)]
[(18, 1), (22, 1), (33, 1), (53, 1), (67, 3), (74, 2), (77, 7), (83, 1), (98, 1), (100, 7), (132, 1), (188, 1), (190, 2), (197, 3), (214, 1), (228, 1), (237, 1), (269, 2), (274, 1), (292, 1), (297, 1)]
[(18, 1), (22, 1), (33, 1), (53, 1), (67, 3), (74, 2), (77, 7), (83, 1), (98, 1), (100, 7), (132, 1), (188, 1), (190, 2), (197, 3), (214, 1), (228, 1), (237, 1), 

[(17, 1), (43, 1), (53, 1), (67, 2), (68, 3), (81, 1), (100, 7), (122, 2), (131, 1), (145, 1), (160, 1), (183, 7), (204, 1), (211, 1), (216, 1), (225, 1), (226, 1), (240, 2), (258, 3), (268, 1)]
[(4, 1), (7, 1), (15, 1), (45, 1), (52, 1), (66, 1), (70, 1), (76, 2), (87, 1), (94, 1), (108, 1), (117, 1), (122, 2), (154, 6), (160, 1), (178, 1), (183, 7), (184, 2), (196, 1), (232, 1), (245, 1), (249, 1), (271, 2), (276, 2)]
[(4, 1), (7, 1), (15, 1), (45, 1), (52, 1), (66, 1), (70, 1), (76, 2), (87, 1), (94, 1), (108, 1), (117, 1), (122, 2), (154, 6), (160, 1), (178, 1), (183, 7), (184, 2), (196, 1), (232, 1), (245, 1), (249, 1), (271, 2), (276, 2)]
[(11, 1), (17, 1), (25, 1), (43, 2), (68, 1), (106, 1), (122, 4), (139, 2), (142, 2), (150, 1), (183, 8), (184, 1), (207, 1), (218, 1), (226, 1), (254, 1), (258, 9), (277, 1), (291, 1)]
[(11, 1), (17, 1), (25, 1), (43, 2), (68, 1), (106, 1), (122, 4), (139, 2), (142, 2), (150, 1), (183, 8), (184, 1), (207, 1), (218, 1), (226, 1), (254, 1), (258,

[(25, 1), (27, 1), (33, 2), (38, 1), (42, 1), (53, 1), (56, 1), (60, 1), (67, 1), (72, 1), (79, 2), (100, 7), (104, 1), (146, 1), (150, 1), (166, 1), (167, 1), (168, 1), (193, 1), (212, 1), (240, 1), (256, 1), (257, 1), (258, 8), (269, 1)]
[(25, 1), (27, 1), (33, 2), (38, 1), (42, 1), (53, 1), (56, 1), (60, 1), (67, 1), (72, 1), (79, 2), (100, 7), (104, 1), (146, 1), (150, 1), (166, 1), (167, 1), (168, 1), (193, 1), (212, 1), (240, 1), (256, 1), (257, 1), (258, 8), (269, 1)]
[(11, 2), (17, 1), (25, 1), (26, 1), (43, 1), (45, 1), (56, 1), (58, 1), (70, 1), (103, 1), (122, 1), (138, 1), (160, 1), (172, 1), (178, 1), (183, 8), (184, 1), (207, 1), (226, 2), (254, 3), (258, 8), (291, 1)]
[(11, 2), (17, 1), (25, 1), (26, 1), (43, 1), (45, 1), (56, 1), (58, 1), (70, 1), (103, 1), (122, 1), (138, 1), (160, 1), (172, 1), (178, 1), (183, 8), (184, 1), (207, 1), (226, 2), (254, 3), (258, 8), (291, 1)]
[(11, 2), (17, 1), (25, 1), (26, 1), (43, 1), (45, 1), (56, 1), (58, 1), (70, 1), (103, 1), (122

[(18, 1), (34, 1), (45, 1), (63, 1), (68, 1), (73, 1), (77, 7), (83, 1), (100, 1), (113, 1), (114, 1), (122, 1), (135, 1), (154, 1), (160, 1), (183, 6), (190, 2), (200, 1), (226, 1), (251, 1), (254, 1), (267, 3), (268, 2), (272, 1), (293, 1)]
[(18, 1), (34, 1), (45, 1), (63, 1), (68, 1), (73, 1), (77, 7), (83, 1), (100, 1), (113, 2), (114, 1), (122, 1), (135, 1), (154, 1), (160, 1), (183, 6), (190, 2), (200, 1), (226, 1), (251, 1), (254, 1), (267, 2), (268, 2), (272, 1), (293, 1)]
[(18, 1), (34, 1), (45, 1), (63, 1), (68, 1), (73, 1), (77, 7), (83, 1), (100, 1), (113, 2), (114, 1), (122, 1), (135, 1), (154, 1), (160, 1), (183, 6), (190, 2), (200, 1), (226, 1), (251, 1), (254, 1), (267, 2), (268, 2), (272, 1), (293, 1)]
[(12, 1), (31, 1), (33, 1), (54, 1), (67, 1), (77, 8), (83, 1), (98, 1), (100, 8), (102, 2), (131, 1), (154, 1), (157, 1), (190, 1), (197, 1), (200, 1), (203, 2), (204, 2), (237, 2), (252, 1), (297, 1), (299, 1)]
[(22, 1), (33, 1), (38, 1), (53, 2), (67, 4), (77, 7), (83

[(7, 2), (15, 2), (33, 1), (36, 1), (38, 1), (52, 1), (66, 1), (76, 1), (87, 1), (100, 7), (104, 1), (117, 1), (154, 7), (192, 1), (212, 1), (216, 2), (222, 1), (233, 1), (235, 1), (254, 1), (257, 1), (260, 1), (269, 1), (275, 1)]
[(24, 1), (26, 1), (45, 1), (58, 1), (63, 1), (68, 2), (70, 2), (71, 1), (72, 1), (79, 1), (106, 2), (108, 2), (122, 1), (160, 1), (183, 6), (184, 2), (186, 2), (211, 1), (232, 2), (256, 1), (258, 6), (261, 1), (268, 1)]
[(24, 1), (26, 1), (45, 1), (58, 1), (63, 1), (68, 2), (70, 2), (71, 1), (72, 1), (79, 1), (106, 2), (108, 2), (122, 1), (160, 1), (183, 6), (184, 2), (186, 2), (211, 1), (232, 2), (256, 1), (258, 6), (261, 1), (268, 1)]
[(25, 1), (56, 1), (66, 1), (71, 1), (72, 1), (75, 1), (76, 1), (87, 1), (117, 1), (139, 1), (154, 6), (159, 1), (160, 1), (183, 4), (187, 2), (200, 1), (221, 1), (222, 1), (226, 1), (245, 1), (254, 3), (256, 1), (258, 5), (260, 1), (275, 1)]
[(25, 1), (44, 1), (56, 1), (60, 1), (66, 1), (72, 1), (75, 1), (76, 1), (87, 1), (1

...

[(22, 1), (24, 1), (33, 1), (53, 1), (74, 1), (77, 7), (83, 1), (98, 1), (100, 6), (102, 1), (114, 1), (131, 1), (132, 1), (145, 2), (153, 2), (188, 1), (190, 1), (197, 2), (237, 2), (240, 1), (254, 1), (258, 1), (265, 1), (286, 1), (296, 1)]
[(22, 1), (24, 1), (33, 1), (53, 1), (74, 1), (77, 7), (83, 1), (98, 1), (100, 6), (102, 1), (114, 1), (131, 1), (132, 1), (145, 2), (153, 2), (188, 1), (190, 1), (197, 2), (237, 2), (240, 1), (254, 1), (258, 1), (265, 1), (286, 1), (296, 1)]
[(22, 1), (24, 1), (33, 1), (53, 1), (74, 1), (77, 7), (83, 1), (98, 1), (100, 6), (102, 1), (114, 1), (131, 1), (132, 1), (145, 2), (153, 2), (188, 1), (190, 1), (197, 2), (237, 2), (240, 1), (254, 1), (258, 1), (265, 1), (286, 1), (296, 1)]
[(18, 1), (22, 1), (36, 1), (48, 1), (53, 2), (77, 7), (83, 1), (98, 1), (100, 7), (101, 1), (102, 1), (114, 1), (118, 1), (157, 1), (190, 1), (225, 1), (240, 1), (265, 2), (269, 1), (272, 2), (281, 2), (286, 1), (297, 2)]
[(18, 1), (22, 1), (36, 1), (48, 1), (53, 2), (7

[(15, 1), (66, 1), (69, 2), (72, 1), (76, 1), (84, 1), (87, 1), (94, 1), (139, 1), (150, 1), (154, 9), (166, 2), (187, 1), (199, 1), (212, 1), (219, 1), (221, 1), (256, 1), (258, 7), (260, 2), (271, 1), (291, 1), (304, 1)]
[(15, 1), (66, 1), (69, 2), (72, 1), (76, 1), (84, 1), (87, 1), (94, 1), (139, 1), (150, 1), (154, 9), (166, 2), (187, 1), (199, 1), (212, 1), (219, 1), (221, 1), (256, 1), (258, 7), (260, 2), (271, 1), (291, 1), (304, 1)]
[(15, 1), (66, 1), (69, 2), (72, 1), (76, 1), (84, 1), (87, 1), (94, 1), (139, 1), (150, 1), (154, 9), (166, 2), (187, 1), (199, 1), (212, 1), (219, 1), (221, 1), (256, 1), (258, 7), (260, 2), (271, 1), (291, 1), (304, 1)]
[(12, 1), (33, 1), (53, 1), (56, 1), (58, 1), (62, 1), (67, 1), (69, 3), (72, 1), (80, 1), (100, 7), (104, 1), (139, 1), (150, 2), (166, 1), (167, 2), (193, 1), (243, 1), (258, 9), (261, 1), (273, 1), (277, 1)]
[(12, 1), (33, 1), (53, 1), (56, 1), (58, 1), (62, 1), (67, 1), (69, 3), (72, 1), (80, 1), (100, 7), (104, 1), (139, 1),

[(0, 2), (22, 1), (25, 1), (26, 1), (56, 2), (58, 1), (60, 1), (81, 1), (93, 1), (104, 1), (108, 1), (122, 1), (138, 1), (160, 1), (165, 1), (166, 1), (168, 1), (183, 3), (193, 1), (207, 1), (212, 1), (218, 1), (228, 1), (232, 1), (237, 1), (243, 1), (256, 1), (258, 7), (268, 1), (304, 1)]
[(0, 2), (22, 1), (25, 1), (26, 1), (56, 2), (58, 1), (60, 1), (81, 1), (93, 1), (104, 1), (108, 1), (122, 1), (138, 1), (160, 1), (165, 1), (166, 1), (168, 1), (183, 3), (193, 1), (207, 1), (212, 1), (218, 1), (228, 1), (232, 1), (237, 1), (243, 1), (256, 1), (258, 7), (268, 1), (304, 1)]
[(44, 1), (45, 1), (52, 1), (66, 3), (87, 1), (94, 1), (110, 1), (117, 2), (124, 1), (154, 6), (160, 1), (163, 1), (178, 1), (183, 6), (184, 1), (194, 1), (208, 1), (211, 2), (218, 1), (226, 1), (229, 2), (249, 1), (254, 1), (268, 1), (271, 1)]
[(44, 1), (45, 1), (52, 1), (66, 3), (87, 1), (94, 1), (110, 1), (117, 2), (124, 1), (154, 6), (160, 1), (163, 1), (178, 1), (183, 6), (184, 1), (194, 1), (208, 1), (211, 2)

[(15, 1), (45, 1), (63, 2), (66, 1), (71, 1), (75, 2), (87, 2), (103, 1), (122, 1), (154, 7), (163, 1), (178, 2), (183, 7), (184, 2), (200, 1), (206, 1), (222, 1), (242, 1), (249, 1), (253, 1), (275, 2), (276, 1)]
[(7, 1), (35, 1), (44, 3), (66, 3), (87, 1), (106, 2), (108, 1), (121, 1), (138, 1), (154, 7), (162, 1), (178, 1), (183, 7), (192, 1), (196, 1), (200, 1), (211, 2), (218, 1), (221, 1), (242, 1), (271, 2)]
[(7, 1), (35, 1), (44, 3), (66, 3), (87, 1), (106, 2), (108, 1), (121, 1), (138, 1), (154, 7), (162, 1), (178, 1), (183, 7), (192, 1), (196, 1), (200, 1), (211, 2), (218, 1), (221, 1), (242, 1), (271, 2)]
[(7, 1), (35, 1), (44, 3), (66, 3), (87, 1), (106, 2), (108, 1), (121, 1), (138, 1), (154, 7), (162, 1), (178, 1), (183, 7), (192, 1), (196, 1), (200, 1), (211, 2), (218, 1), (221, 1), (242, 1), (271, 2)]
[(18, 2), (26, 1), (34, 1), (44, 1), (77, 6), (83, 1), (85, 1), (91, 1), (100, 2), (118, 1), (130, 1), (132, 1), (148, 1), (153, 1), (180, 1), (190, 2), (252, 1), (258, 5)

[(18, 1), (27, 2), (30, 1), (43, 1), (58, 1), (72, 2), (77, 1), (79, 3), (108, 1), (112, 1), (120, 1), (142, 3), (169, 1), (176, 1), (183, 6), (195, 1), (207, 1), (226, 1), (239, 2), (256, 1), (258, 7), (304, 1)]
[(18, 1), (27, 2), (30, 1), (43, 1), (58, 1), (72, 2), (77, 1), (79, 3), (108, 1), (112, 1), (120, 1), (142, 3), (169, 1), (176, 1), (183, 6), (195, 1), (207, 1), (226, 1), (239, 2), (256, 1), (258, 7), (304, 1)]
[(54, 1), (56, 1), (62, 2), (69, 1), (72, 3), (77, 8), (79, 1), (85, 1), (89, 2), (95, 1), (97, 1), (153, 1), (170, 1), (237, 2), (252, 1), (256, 1), (258, 9), (291, 2), (304, 1)]
[(33, 1), (34, 1), (67, 2), (74, 2), (77, 9), (96, 1), (100, 9), (129, 1), (145, 1), (148, 2), (188, 2), (197, 2), (204, 1), (216, 1), (237, 1), (240, 2), (257, 1), (286, 1)]
[(33, 1), (34, 1), (67, 2), (74, 2), (77, 9), (96, 1), (100, 9), (129, 1), (145, 1), (148, 2), (188, 2), (197, 2), (204, 1), (216, 1), (237, 1), (240, 2), (257, 1), (286, 1)]
[(0, 1), (12, 2), (22, 2), (33, 2), (67, 1),

In [13]:
#number of unique cards in set
unique_cards = len(dictionary.keys())
print(unique_cards)

305


In [14]:
#setting the hyperparameters of the model
archetypes = 15
np.random.seed(1)
alpha_prior = [1.0 / archetypes] * archetypes
beta_prior = [1.0 / archetypes] * unique_cards

In [15]:
#running model
iterations = 40
#my machine has 8 cores, so using 7 for the ldamulticore model
num_cores=7
#also using the ldamodel so I can auto assign alpha and eta
# lda = gensim.models.ldamodel.LdaModel(corpus=win_corpus, id2word=dictionary, num_topics=archetypes, passes=iterations, alpha = "symmetric", eta = "auto")
lda = gensim.models.ldamulticore.LdaMulticore(workers=num_cores,corpus=win_corpus, id2word=dictionary, num_topics=archetypes, passes=iterations, alpha = alpha_prior, eta = beta_prior)

In [16]:
number_of_top_cards = 25
archetypes_to_inspect = archetypes
for i in range(archetypes_to_inspect):
    print(("Archetype %i \n %s \n") % (i, lda.print_topic(i, topn=number_of_top_cards)))

Archetype 0 
 0.112*"Base Camp" + 0.108*"Lithoform Engine" + 0.068*"Swamp" + 0.063*"Lithoform Blight" + 0.044*"Brightclimb Pathway" + 0.043*"Stonework Packbeast" + 0.040*"Sea Gate Colossus" + 0.036*"Plains" + 0.029*"Skyclave Relic" + 0.026*"Relic Golem" + 0.023*"Relic Axe" + 0.023*"Beyeen Veil" + 0.022*"Deadly Alliance" + 0.020*"Zareth San, the Trickster" + 0.020*"Tazri, Beacon of Unity" + 0.020*"Skyclave Cleric" + 0.019*"Clearwater Pathway" + 0.019*"Jwari Disruption" + 0.018*"Coveted Prize" + 0.016*"Pelakka Predation" + 0.012*"Sejiri Shelter" + 0.012*"Felidar Retreat" + 0.010*"Skyclave Sentinel" + 0.010*"Throne of Makindi" + 0.010*"Linvala, Shield of Sea Gate" 

Archetype 1 
 0.207*"Plains" + 0.181*"Mountain" + 0.032*"Expedition Champion" + 0.031*"Cliffhaven Sell-Sword" + 0.030*"Kargan Warleader" + 0.030*"Kor Blademaster" + 0.022*"Sea Gate Banneret" + 0.021*"Relic Axe" + 0.021*"Grotag Bug-Catcher" + 0.021*"Resolute Strike" + 0.020*"Cliffhaven Kitesail" + 0.018*"Scavenged Blade" + 0.01

In [17]:
#can use this to predict achetype based on deck comp
#could be useful in adjusting weights for a draft bot
lda.get_document_topics([(25, 1), (27, 1), (56, 1), (69, 1), (72, 1), (75, 1), (76, 1), (84, 1), (87, 3), (139, 1), (142, 2), (152, 1), (154, 8), (189, 1), (258, 8), (260, 1), (275, 1), (276, 1), (288, 1), (291, 1)])

[(2, 0.5280579), (10, 0.44913477)]

In [20]:
lda.top_topics(win_corpus,dictionary=dictionary)

[([(0.3711832, 'Mountain'),
   (0.054431282, 'Grotag Bug-Catcher'),
   (0.054090597, 'Ardent Electromancer'),
   (0.04835337, 'Roil Eruption'),
   (0.045503877, 'Fissure Wizard'),
   (0.024899496, 'Expedition Champion'),
   (0.024494983, 'Pyroclastic Hellion'),
   (0.024371099, 'Synchronized Spellcraft'),
   (0.023031134, 'Rockslide Sorcerer'),
   (0.021806424, 'Stonework Packbeast'),
   (0.021715619, 'Sneaking Guide'),
   (0.018383449, 'Thundering Sparkmage'),
   (0.017412642, 'Teeterpeak Ambusher'),
   (0.016806684, "Kazuul's Fury"),
   (0.01680301, 'Akoum Warrior'),
   (0.015484898, 'Shatterskull Minotaur'),
   (0.014964382, 'Spikefield Hazard'),
   (0.014832096, 'Scorch Rider'),
   (0.014298211, 'Thundering Rebuke'),
   (0.013165509, 'Song-Mad Treachery')],
  -1.214061386548288),
 ([(0.4012527, 'Swamp'),
   (0.04217432, 'Expedition Skulker'),
   (0.041221127, 'Malakir Blood-Priest'),
   (0.038655918, 'Deadly Alliance'),
   (0.03855038, 'Nimana Skydancer'),
   (0.034631476, 'Vanquis

In [18]:
archetype_id = 5
archetype_topic = np.array(lda.show_topic(archetype_id, topn=9999))

archetype_distribution = np.array(archetype_topic[:,1], dtype="float32")
archetype_distribution = archetype_distribution / np.sum(archetype_distribution)

archetype_indices = np.zeros(len(archetype_distribution))
main_deck = 60
sideboard = 15
while np.sum(archetype_indices) < main_deck+sideboard:
    new_card = np.random.multinomial(1, archetype_distribution)
    archetype_indices += new_card
#     if 5 in archetype_indices:
#         archetype_indices -= new_card
archetype_cards = np.array(archetype_topic[:,0])
minimum_cards = 1.0
deck_title = "Whatever Achetype 5 is"
print(deck_title)
for i in range(len(archetype_distribution)):
    if archetype_indices[i] >= minimum_cards:        
        print('%i %s' % (archetype_indices[i], archetype_cards[i]))

Whatever Achetype 5 is
24 Plains
7 Prowling Felidar
9 Tazeem Raptor
1 Makindi Ox
2 Fearless Fledgling
4 Canyon Jerboa
3 Cliffhaven Sell-Sword
2 Farsight Adept
1 Mesa Lynx
1 Smite the Monstrous
2 Practiced Tactics
2 Sea Gate Banneret
2 Resolute Strike
1 Kabira Takedown
3 Expedition Healer
1 Angelheart Protector
1 Kitesail Cleric
1 Paired Tactician
4 Tazri, Beacon of Unity
1 Journey to Oblivion
1 Kabira Outrider
2 Spare Supplies


In [ ]:
#implementing code from https://towardsdatascience.com/evaluate-topic-model-in-python-latent-dirichlet-allocation-lda-7d57484bb5d0

In [31]:
# supporting function
def compute_coherence_values(corpus, dictionary, k, a, b):
    lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                           id2word=dictionary,
                                           num_topics=k, 
                                           random_state=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=a,
                                           eta=b)
    
    coherence_model_lda = CoherenceModel(model=lda_model, texts=corpus, dictionary=dictionary, coherence='c_v')
    
    return coherence_model_lda.get_coherence()

In [ ]:
import tqdm
from gensim.models import CoherenceModel
grid = {}
grid['Validation_Set'] = {}
# Topics range
min_topics = 10
max_topics = 20
step_size = 1
topics_range = range(min_topics, max_topics, step_size)
# Alpha parameter
alpha = list(np.arange(0.01, 1, 0.3))
alpha.append('symmetric')
alpha.append('asymmetric')
# Beta parameter
beta = list(np.arange(0.01, 1, 0.3))
beta.append('symmetric')
# Validation sets
#num_of_docs = len(all_corpus)
corpus_sets = [# gensim.utils.ClippedCorpus(corpus, num_of_docs*0.25), 
               # gensim.utils.ClippedCorpus(corpus, num_of_docs*0.5), 
               #gensim.utils.ClippedCorpus(corpus, num_of_docs*0.75), 
               all_corpus]

corpus_title = ['75% Corpus', '100% Corpus']

model_results = {'Validation_Set': [],
                 'Topics': [],
                 'Alpha': [],
                 'Beta': [],
                 'Coherence': []
                }
# Can take a long time to run
#if 1 == 1:
    pbar = tqdm.tqdm(total=540)
    
    # iterate through validation corpuses
    for i in range(len(corpus_sets)):
        # iterate through number of topics
        for k in topics_range:
            # iterate through alpha values
            for a in alpha:
                # iterare through beta values
                for b in beta:
                    # get the coherence score for the given parameters
                    cv = compute_coherence_values(corpus=corpus_sets[i], dictionary=dictionary, 
                                                  k=k, a=a, b=b)
                    # Save the model results
                    model_results['Validation_Set'].append(corpus_title[i])
                    model_results['Topics'].append(k)
                    model_results['Alpha'].append(a)
                    model_results['Beta'].append(b)
                    model_results['Coherence'].append(cv)
                    
                    pbar.update(1)
    pd.DataFrame(model_results).to_csv('lda_tuning_results.csv', index=False)
    pbar.close()




  0%|                                                                                          | 0/540 [00:00<?, ?it/s]C:\Users\gamui\anaconda3\lib\site-packages\gensim\topic_coherence\direct_confirmation_measure.py:202: RuntimeWarning: invalid value encountered in true_divide
  numerator = (co_occur_count / num_docs) + EPSILON
C:\Users\gamui\anaconda3\lib\site-packages\gensim\topic_coherence\direct_confirmation_measure.py:203: RuntimeWarning: invalid value encountered in true_divide
  denominator = (w_prime_count / num_docs) * (w_star_count / num_docs)
C:\Users\gamui\anaconda3\lib\site-packages\gensim\topic_coherence\direct_confirmation_measure.py:198: RuntimeWarning: invalid value encountered in true_divide
  co_doc_prob = co_occur_count / num_docs



  0%|▏                                                                              | 1/540 [01:22<12:20:23, 82.42s/it]


  0%|▎                                                                              | 2/540 [02:48<12:28:27, 83

In [33]:
cv = compute_coherence_values(corpus=all_corpus, dictionary=dictionary, 
                                                  k=archetypes, a="asymmetric", b=beta_prior)
cv

C:\Users\gamui\anaconda3\lib\site-packages\gensim\topic_coherence\direct_confirmation_measure.py:202: RuntimeWarning: invalid value encountered in true_divide
  numerator = (co_occur_count / num_docs) + EPSILON
C:\Users\gamui\anaconda3\lib\site-packages\gensim\topic_coherence\direct_confirmation_measure.py:203: RuntimeWarning: invalid value encountered in true_divide
  denominator = (w_prime_count / num_docs) * (w_star_count / num_docs)
C:\Users\gamui\anaconda3\lib\site-packages\gensim\topic_coherence\direct_confirmation_measure.py:198: RuntimeWarning: invalid value encountered in true_divide
  co_doc_prob = co_occur_count / num_docs


nan